This Scala notebook uses *BeakerX*, a Two Sigma Open Source project that enhances Jupyter.

<http://beakerx.com/>

In [1]:
scala.util.Properties.versionMsg

Scala library version 2.11.12 -- Copyright 2002-2017, LAMP/EPFL

![Magic the Gathering](https://media.wizards.com/2018/images/daily/gcYrmy5q9f.png)

As an example of using Scala traits for mix-in functionality,
we'll implement some simple classes representing Magic the Gathering creatures with mix-in abilities.

Cards and other images are linked from <https://magic.wizards.com/>, &copy; Wizards of the Coast LLC.

# Mana

![Mana Colors](https://media.magic.wizards.com/image_legacy_migration/mtg/images/daily/ftl/ftl87_wubrg.jpg)

In [2]:
object Color {
    case object White extends Color
    case object Blue extends Color
    case object Black extends Color
    case object Red extends Color
    case object Green extends Color
    case object Generic extends Color
    case object Colorless extends Color
}

sealed abstract class Color

defined object Color
defined class Color


## Card States

![Tapped](http://media.wizards.com/images/magic/daily/td/td107_attacking.jpg)

In [3]:
object State {
    case object Library extends State
    case object Hand extends State
    case object Tapped extends State
    case object Untapped extends State
    case object Graveyard extends State
    case object Exile extends State
}

sealed abstract class State

defined object State
defined class State


# Cards

![MTG Hand](http://media.wizards.com/2016/images/daily/eRLeVGuciF.png)

In [4]:
abstract class Card {
    /** The mana cost to play this card */
    def cost: Map[Color, Int]
    
    /** State card enters after it is played */
    def postPlayState: State
}

defined class Card


## Sorceries

In [5]:
abstract class Sorcery extends Card {
    /** Sorceries are discarded after being played */
    def postPlayState = State.Graveyard
}

defined class Sorcery


## Creatures

In [6]:
abstract class Creature(
    /** Creature's summoning cost */
    val cost: Map[Color, Int],
    /** Creature's attack power */
    val power: Int,
    /** Creature's defensive toughness */
    val toughness: Int) extends Card {
    
    /**
     * Check if other creature can block this creature's attacks.
     * By default, any creature can block any other creature.
     */
    def isBlockableBy(other: Creature): Boolean = true
    
    /**
     * Check if this creature can attack in the given state.
     * By default, creatures can attack iff untapped.
     */
    def canAttack(currentState: State): Boolean =
        currentState == State.Untapped
    
    /**
     * Early (first-strike) combat damage.
     * By default, creatures don't deal early damage.
     */
    def earlyCombatDamange: Option[Int] = None
    
    /**
     * Normal (non-first-strike) combat damage.
     * By default, this is equal to the creature's power.
     */
    def normalCombatDamange: Option[Int] = Some(power)
    
    /** Creatures enter the battlefield with summoning sickness */
    def postPlayState = State.Tapped
}

defined class Creature


# Abilities

## Reach & Flying

In [7]:
trait Reach { this: Creature => }

defined trait Reach


In [8]:
trait Flying { this: Creature =>
    /**
     * Flying creatures can only be blocked by
     * other Flying creatures or by creatures with Reach.
     */
    override def isBlockableBy(other: Creature): Boolean = other match {
        case (_: Flying) | (_: Reach) => true
        case _ => false
    }
}

defined trait Flying


## Defender

In [9]:
trait Defender { this: Creature =>
    /** Defenders can never attack */
    override def canAttack(currentState: State) = false
}

defined trait Defender


## First-strike

In [10]:
trait FirstStrike { this: Creature =>
    /** Creatures with first-strike deal damage early. */
    override def earlyCombatDamange: Option[Int] = Some(power)
    
    /** Creatures with first-strike deal no normal damage. */
    override def normalCombatDamange: Option[Int] = None
}

defined trait FirstStrike


## Double-strike

In [11]:
trait DoubleStrike { this: Creature =>
    /** Creatures with double-strike deal early AND normal damage. */
    override def earlyCombatDamange: Option[Int] = Some(power)
}

defined trait DoubleStrike


## Haste

In [12]:
trait Haste { this: Creature =>
    /** Creatures with haste enter battle untapped. */
    override def postPlayState = State.Untapped
}

defined trait Haste


# Implementing Cards with Abilities

## Bartizan Bats

[![Bartizan Bats](https://gatherer.wizards.com/Handlers/Image.ashx?multiverseid=469872&type=card)](https://gatherer.wizards.com/Pages/Card/Details.aspx?multiverseid=469872)

In [13]:
case object BartizanBats extends Creature(Map(Color.Generic->3, Color.Black->1), 3, 1) with Flying

BartizanBats

## Canopy Spider

[![Canopy Spider](https://gatherer.wizards.com/Handlers/Image.ashx?multiverseid=469892&type=card)](https://gatherer.wizards.com/Pages/Card/Details.aspx?multiverseid=469892)

In [14]:
case object CanopySpider extends Creature(Map(Color.Generic->1, Color.Green->1), 1, 3) with Reach

CanopySpider

## Minotaur Aggressor

[![Minotaur Aggressor](https://gatherer.wizards.com/Handlers/Image.ashx?multiverseid=270800&type=card)](https://gatherer.wizards.com/Pages/Card/Details.aspx?multiverseid=270800)

In [15]:
case object MinotaurAggressor extends Creature(Map(Color.Generic->6, Color.Red->1), 6, 2) with FirstStrike with Haste

MinotaurAggressor

## Skyhunter Skirmisher

[![Skyhunter Skirmisher](https://gatherer.wizards.com/Handlers/Image.ashx?multiverseid=397835&type=card)](https://gatherer.wizards.com/Pages/Card/Details.aspx?multiverseid=397835)

In [16]:
case object SkyhunterSkirmisher extends Creature(Map(Color.Generic->1, Color.White->2), 1, 1) with Flying with DoubleStrike

SkyhunterSkirmisher

## Wall of Swords

[![Wall of Swords](https://gatherer.wizards.com/Handlers/Image.ashx?multiverseid=370697&type=card)](https://gatherer.wizards.com/Pages/Card/Details.aspx?multiverseid=29772)

In [17]:
case object WallOfSwords extends Creature(Map(Color.Generic->3, Color.White->1), 3, 5) with Defender with Flying

WallOfSwords

## Woodland Druid

[![Woodland Druid](https://gatherer.wizards.com/Handlers/Image.ashx?multiverseid=29772&type=card)](https://gatherer.wizards.com/Pages/Card/Details.aspx?multiverseid=370697)

In [18]:
case object WoodlandDruid extends Creature(Map(Color.Green->1), 1, 2)

WoodlandDruid

# Allowed to Block?

In [19]:
SkyhunterSkirmisher isBlockableBy MinotaurAggressor  // Flying vs Normal

false

In [20]:
SkyhunterSkirmisher isBlockableBy CanopySpider  // Flying vs Reach

true

In [21]:
WoodlandDruid isBlockableBy WallOfSwords  // Flying vs Flying

true

In [22]:
WoodlandDruid isBlockableBy BartizanBats  // Normal vs Flying

true

In [23]:
CanopySpider isBlockableBy WoodlandDruid  // Reach vs Normal

true

In [24]:
MinotaurAggressor isBlockableBy CanopySpider  // Normal vs Reach

true